**Problemática Abordada**

La empresa Riemax Inmobiliaria, una agencia con operaciones globales dedicada a la intermediación en la compra y venta de propiedades, enfrenta actualmente desafíos significativos en la gestión de su portafolio de transacciones. La información crítica sobre las propiedades listadas (ubicación, características, precio), las evaluaciones del entorno (índices de conectividad, calificaciones de vecindario) y los perfiles financieros de los clientes (salarios, montos de préstamos, decisiones finales) se encuentra fragmentada. Estos datos están dispersos en múltiples archivos de hojas de cálculo y reportes locales en diferentes oficinas internacionales, dificultando tener un inventario unificado y consultar el historial de operaciones de forma fiable.

**Objetivo**

Implementar una base de datos relacional centralizada para Riemax Inmobiliaria. El propósito principal es migrar e integrar toda la información histórica existente sobre las propiedades, las evaluaciones de entorno y las decisiones de compra de los clientes en esta nueva estructura unificada. Esta solución permitirá a la empresa organizar y consolidar sus registros, asegurando la integridad de los datos y mejorando la eficiencia en la gestión y consulta de la información operativa de las transacciones pasadas.

**Dataset** 


Nombre: Global House Purchase Decision Dataset
Fuente: Global Property Purchase Decision Dataset
Enlace: https://www.kaggle.com/datasets/mohankrishnathalla/global-house-purchase-decision-dataset?resource=download

**🎯 Variables Relevantes **

1. decision (Decisión)

Por qué es relevante: Es la variable clave para un análisis de clasificación. Te permite construir modelos para predecir si una futura solicitud de préstamo será aprobada (1) o rechazada (0), basándote en todas las demás variables financieras y de propiedad.

2. price (Precio)

Por qué es relevante: Es la variable objetivo para un análisis de regresión. Te permite entender qué factores (como el tamaño, la ubicación o el año de construcción) influyen más en el precio de una propiedad.

3. emi_to_income_ratio (Ratio EMI/Ingresos)

Por qué es relevante: Esta es quizás la variable financiera más potente. Mide la asequibilidad. Un banco no mira solo cuánto ganas (customer_salary) o cuánto pides (loan_amount), sino la relación entre ambos. Un ratio alto (ej. 50% de tu salario se va al préstamo) es un indicador de alto riesgo y probablemente predice un decision = 0.

4. customer_salary (Salario del Cliente)

Por qué es relevante: Es el pilar del análisis financiero. Determina el poder adquisitivo general. Es fundamental para predecir tanto el price de la vivienda que una persona puede permitirse como la decision final del préstamo.

5. property_size_sqft (Tamaño de la Propiedad)

Por qué es relevante: Es uno de los predictores físicos más directos del price. A mayor tamaño, casi siempre mayor precio (aunque la ubicación modera esto). También puede influir en la decision si el préstamo solicitado no se corresponde con el valor de una propiedad de ese tamaño.

6. neighbourhood_rating (Calificación del Vecindario)

Por qué es relevante: Esta variable captura el valor intangible de la "ubicación". Una calificación alta puede justificar un price elevado incluso para una propiedad pequeña (property_size_sqft) y puede dar más seguridad al banco para aprobar la decision, ya que la propiedad se considera una buena inversión (tiene buen valor de reventa).
 

In [0]:
!pip install kagglehub[pandas-datasets]>=0.3.8

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


##Importamos librerias

In [0]:
import kagglehub
import pandas as pd
import os
import zipfile

Creamos Funciones para Descargar, Extraer y el Leer el Dataset de Kaggle.

In [0]:
def download_dataset_zip(url = ""):
        print("Descargando dataset desde Kaggle...")
        dataset_path = kagglehub.dataset_download(url)
        print("Ruta al dataset:", dataset_path)
        return dataset_path
    
def extract_zip_files(dataset_path):
        zip_files = [f for f in os.listdir(dataset_path) if f.endswith('.zip')]
        if zip_files:
            zip_file = os.path.join(dataset_path, zip_files[0])
            extract_dir = os.path.join(dataset_path, "extracted")
            os.makedirs(extract_dir, exist_ok=True)
            print(f"Extrayendo {zip_file} en {extract_dir}...")
            with zipfile.ZipFile(zip_file, "r") as z:
                z.extractall(extract_dir)
            return extract_dir
        else:
            # Si no se encuentra un ZIP, se verifica si existen archivos CSV en la ruta
            csv_files = [f for f in os.listdir(dataset_path) if f.endswith('.csv')]
            if csv_files:
                print("No se encontró archivo ZIP pero se detectaron archivos CSV; se asume que el dataset ya se encuentra extraído.")
                return dataset_path
            else:
                raise FileNotFoundError("No se encontró ningún archivo .zip ni archivos .csv en la ruta del dataset")

def create_csv(csv_dir, csv_name=None):
    if csv_name:
        file_path = os.path.join(csv_dir, csv_name)
        print(f"Leyendo {file_path}...")
        df = pd.read_csv(file_path, encoding="latin1")
        print("CSV creado correctamente")
        return df
    else:
        csv_files = [f for f in os.listdir(csv_dir) if f.endswith('.csv')]
        if not csv_files:
            raise FileNotFoundError("No se encontraron archivos CSV en el directorio extraído")
        for file in csv_files:
            file_path = os.path.join(csv_dir, file)
            print(f"Leyendo {file_path}...")
            df = pd.read_csv(file_path, encoding="latin1")
        print("CSV creado correctamente")
        return df


Descargamos dataset

In [0]:
df = pd.DataFrame()
dataset_path = download_dataset_zip("mohankrishnathalla/global-house-purchase-decision-dataset") 
csv_dir = extract_zip_files(dataset_path)
df = create_csv(csv_dir)

Descargando dataset desde Kaggle...
Ruta al dataset: /home/spark-a6855972-9657-46e0-8528-b7/.cache/kagglehub/datasets/mohankrishnathalla/global-house-purchase-decision-dataset/versions/1
No se encontró archivo ZIP pero se detectaron archivos CSV; se asume que el dataset ya se encuentra extraído.
Leyendo /home/spark-a6855972-9657-46e0-8528-b7/.cache/kagglehub/datasets/mohankrishnathalla/global-house-purchase-decision-dataset/versions/1/global_house_purchase_dataset.csv...
CSV creado correctamente


Validamos DF

In [0]:
df.head(5)

property_id       country  ... connectivity_score decision
0            1        France  ...                  6        0
1            2  South Africa  ...                  2        0
2            3  South Africa  ...                  1        0
3            4       Germany  ...                  6        0
4            5  South Africa  ...                  4        0

[5 rows x 25 columns]

Convertimos de pandas a Spark

In [0]:
spark_df = spark.createDataFrame(df)

Creamos la Tabla e Insertamos datos

In [0]:
spark_df.write.mode("overwrite").saveAsTable("tbl_ventas_viviendas")

Verificamos la creación de la tabla con sus variables

In [0]:
%sql
DESCRIBE TABLE tbl_ventas_viviendas;

col_name data_type comment property_id bigint null country string null city string null property_type string null furnishing_status string null property_size_sqft bigint null price bigint null constructed_year bigint null previous_owners bigint null rooms bigint null bathrooms bigint null garage bigint null garden bigint null crime_cases_reported bigint null legal_cases_on_property bigint null customer_salary bigint null loan_amount bigint null loan_tenure_years bigint null monthly_expenses bigint null down_payment bigint null emi_to_income_ratio double null satisfaction_score bigint null neighbourhood_rating bigint null connectivity_score bigint null decision bigint null

Contamos 10 registros

In [0]:
%sql
SELECT * 
FROM tbl_ventas_viviendas
LIMIT 10;
     

property_id country city property_type furnishing_status property_size_sqft price constructed_year previous_owners rooms bathrooms garage garden crime_cases_reported legal_cases_on_property customer_salary loan_amount loan_tenure_years monthly_expenses down_payment emi_to_income_ratio satisfaction_score neighbourhood_rating connectivity_score decision 1 France Marseille Farmhouse Semi-Furnished 991 412935 1989 6 6 2 1 1 1 0 10745 193949 15 6545 218986 0.16 1 5 6 0 2 South Africa Cape Town Apartment Semi-Furnished 1244 224538 1990 4 8 8 1 1 1 1 16970 181465 20 8605 43073 0.08 9 1 2 0 3 South Africa Johannesburg Farmhouse Semi-Furnished 4152 745104 2019 5 2 1 1 1 0 0 21914 307953 30 2510 437151 0.09 6 8 1 0 4 Germany Frankfurt Farmhouse Semi-Furnished 3714 1110959 2008 1 3 3 0 1 0 0 17980 674720 15 8805 436239 0.33 2 6 6 0 5 South Africa Johannesburg Townhouse Fully-Furnished 531 99041 2007 6 3 3 1 1 3 1 17676 65833 25 8965 33208 0.03 3 3 4 0 6 Canada Montreal Villa Semi-Furnished 3169 1107368 1985 0 5 2 1 0 0 0 95520 793316 30 10615 314052 0.05 10 8 2 1 7 Brazil Rio de Janeiro Studio Unfurnished 1986 398439 1976 1 2 1 1 0 0 0 11426 268167 25 14440 130272 0.16 9 10 10 1 8 Brazil SÃ£o Paulo Townhouse Semi-Furnished 4048 807236 2020 4 6 6 1 1 1 0 29832 503385 20 7200 303851 0.13 1 5 8 0 9 UAE Dubai Farmhouse Semi-Furnished 5213 3131373 1968 6 2 1 0 0 0 0 56255 1866416 15 10300 1264957 0.29 8 8 10 1 10 Australia Melbourne Apartment Unfurnished 4648 1483250 1966 2 5 2 0 1 0 1 67350 1093290 10 16360 389960 0.18 1 4 7 0

Conteo de Propiedades por País

In [0]:
%sql
SELECT
    country,
    COUNT(property_id) AS total_propiedades
FROM
    tbl_ventas_viviendas
GROUP BY
    country
ORDER BY
    total_propiedades DESC;

country total_propiedades France 15628 China 15536 Australia 15442 UK 15413 Germany 15408 Canada 15401 South Africa 15401 Brazil 15397 India 15357 Japan 15317 USA 15281 Singapore 15278 UAE 15141

Cuenta cuántas propiedades (viviendas) hay registradas en tu base de datos para cada país y las ordena de mayor a menor.

Propiedades más Caras

In [0]:
%sql
SELECT
    property_id,
    city,
    price
FROM
    tbl_ventas_viviendas
ORDER BY
    price DESC
LIMIT 10;

property_id city price 149437 Singapore 4202732 145267 Singapore 4202721 70487 Singapore 4202151 16744 Singapore 4201912 166138 Singapore 4201277 68167 Singapore 4201197 21063 Singapore 4200900 85180 Singapore 4200894 77251 Singapore 4199892 178596 Singapore 4198888

Muestra el ID, la ciudad y el precio de las 10 viviendas más caras de todo el dataset.

Propiedades donde la Compra fue Aprobada

In [0]:
%sql
SELECT
    *
FROM
    tbl_ventas_viviendas
WHERE
    decision = 1;

property_id country city property_type furnishing_status property_size_sqft price constructed_year previous_owners rooms bathrooms garage garden crime_cases_reported legal_cases_on_property customer_salary loan_amount loan_tenure_years monthly_expenses down_payment emi_to_income_ratio satisfaction_score neighbourhood_rating connectivity_score decision 100002 UK London Apartment Fully-Furnished 1483 594872 1973 3 5 4 0 1 1 0 82460 423894 30 10405 170978 0.03 7 9 9 1 100011 UAE Abu Dhabi Townhouse Fully-Furnished 2447 1463200 2014 1 3 2 1 0 1 0 22655 994781 30 5195 468419 0.28 8 8 9 1 100013 India Hyderabad Independent House Semi-Furnished 4537 683958 1975 1 4 3 1 0 2 0 14555 369137 30 558 314821 0.16 10 5 2 1 100020 India Hyderabad Villa Semi-Furnished 1185 174870 1969 4 4 1 1 0 1 0 10655 128883 10 2627 45987 0.14 10 5 5 1 100024 Germany Frankfurt Apartment Unfurnished 2482 740347 1989 0 1 1 1 0 0 0 85270 360953 20 6980 379394 0.03 8 1 9 1 100040 Canada Montreal Independent House Unfurnished 940 331014 1990 6 8 7 1 1 1 0 46540 264232 25 12570 66782 0.04 8 4 10 1 100043 South Africa Cape Town Townhouse Fully-Furnished 2534 454642 1986 3 1 1 0 0 2 0 18864 309012 30 4910 145630 0.1 9 1 4 1 100050 Germany Berlin Townhouse Fully-Furnished 2027 610976 1988 1 7 2 1 0 0 0 35025 383909 15 19995 227067 0.1 10 10 6 1 100053 China Shanghai Independent House Unfurnished 5837 2221974 2003 3 6 5 0 1 1 0 95595 1673937 20 5965 548037 0.13 8 7 1 1 100056 Japan Tokyo Independent House Fully-Furnished 5152 2317864 2014 0 5 2 0 1 0 0 81330 1246899 20 18280 1070965 0.11 7 9 3 1 100061 Brazil Rio de Janeiro Townhouse Fully-Furnished 2877 579505 1998 1 1 1 1 0 1 0 13184 398585 30 11535 180920 0.19 7 7 6 1 100064 Brazil SÃ£o Paulo Farmhouse Fully-Furnished 553 112777 2017 1 8 1 0 0 2 0 22034 78992 10 13220 33785 0.04 8 5 2 1 100067 UK Birmingham Townhouse Fully-Furnished 3716 1488679 1967 0 3 2 0 0 0 0 86940 1175982 10 3815 312697 0.15 7 10 10 1 100071 China Shanghai Apartment Unfurnished 1051 397078 2004 3 7 6 1 1 1 0 91050 242611 25 15920 154467 0.02 9 3 10 1 100077 China Beijing Studio Fully-Furnished 1335 506133 1996 3 5 5 0 0 2 0 85800 214800 25 10020 291333 0.02 7 7 2 1 100093 Japan Tokyo Farmhouse Fully-Furnished 3774 1695058 1987 5 3 1 1 0 0 0 79810 703914 20 4030 991144 0.07 10 4 1 1 100095 Canada Montreal Independent House Semi-Furnished 1835 646313 1992 3 8 3 1 1 1 0 17525 381124 25 4125 265189 0.15 10 6 10 1 100102 Singapore Singapore Villa Semi-Furnished 2905 2037059 1981 0 8 4 1 1 0 0 76815 1467942 25 5830 569117 0.13 10 6 9 1 100107 Germany Munich Studio Fully-Furnished 3740 1117672 2001 1 4 2 0 1 1 0 14055 654624 20 19135 463048 0.35 7 4 1 1 100113 Japan Kyoto Studio Semi-Furnished 3941 1770280 1990 2 1 1 0 0 1 0 19945 737419 15 17430 1032861 0.32 10 1 8 1 100114 South Africa Cape Town Farmhouse Unfurnished 3867 694722 1977 6 3 1 1 1 2 0 15476 366845 20 16115 327877 0.18 10 7 9 1 100116 Japan Osaka Townhouse Unfurnished 506 229215 1999 2 3 3 0 0 2 0 79720 188490 10 17010 40725 0.03 10 6 1 1 100122 UAE Abu Dhabi Apartment Unfurnished 2081 1244072 2011 2 7 4 0 0 1 0 29975 555318 25 11485 688754 0.13 7 6 8 1 100127 Singapore Singapore Villa Semi-Furnished 4439 3102308 1987 1 7 7 0 0 0 0 72800 1541106 30 11250 1561202 0.13 9 2 2 1 100129 USA Chicago Townhouse Unfurnished 2283 1137147 1981 0 7 7 0 0 0 0 33035 566777 30 11655 570370 0.11 10 10 10 1 100132 Singapore Singapore Farmhouse Semi-Furnished 2867 2005129 2018 6 8 7 0 1 2 0 45020 1452754 10 12410 552375 0.37 8 8 3 1 100139 Australia Sydney Townhouse Unfurnished 4137 1328801 1983 3 2 1 1 0 1 0 72105 1121336 20 11340 207465 0.12 10 8 3 1 100148 UAE Dubai Farmhouse Fully-Furnished 4873 2920002 2020 0 6 2 0 0 0 0 75855 1694137 25 11815 1225865 0.15 10 10 10 1 100154 Japan Osaka Farmhouse Fully-Furnished 1209 541919 1962 0 8 8 1 0 0 0 64770 413964 10 6660 127955 0.07 8 3 4 1 100162 Japan Tokyo Apartment Fully-Furnished 882 394010 1994 5 8 3 1 1 0 0 94195 236683 20 12300 157327 0.02 9 1 4 1 

Selecciona todas las columnas de las filas donde la compra fue exitosa (asumiendo que decision = 1 significa "aprobado", según el dataset).

Precio Promedio por Tipo de Propiedad

In [0]:
%sql
SELECT
    property_type,
    AVG(price) AS precio_promedio
FROM
    tbl_ventas_viviendas
GROUP BY
    property_type;

property_type precio_promedio Townhouse 1216972.455217847 Farmhouse 1220261.5798078645 Studio 1212892.1994970916 Apartment 1216839.2162404933 Villa 1211266.50346358 Independent House 1213903.4250314995

Calcula el precio promedio de venta para cada tipo de propiedad (Apartment, Farmhouse, etc.).